In [1]:
import tensorflow as tf
from tensorflow.examples.tutorials.mnist import input_data
import numpy as np

In [18]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

In [19]:
tf.logging.set_verbosity(tf.logging.INFO)

In [2]:
# Import data
mnist = input_data.read_data_sets('MNIST_data', one_hot=True)

Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST_data\train-images-idx3-ubyte.gz
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST_data\train-labels-idx1-ubyte.gz
Instructions for updating:
Please use tf.one_hot on tensors.
Extracting MNIST_data\t10k-images-idx3-ubyte.gz
Extracting MNIST_data\t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.


In [3]:
#图片的大小为28 * 28 
#filter 

In [4]:
#神经网络结构
#input size [batch_size, 28, 28, 1]
#layer1：卷积层：卷积核大小5 * 5 (经验值)补0后 input size为 32 * 32 的(因为步长为1，且padding模式为same,所以28 * 28的图片，卷积核的边长就是 28 + low(5 / 2) * 2 = 32
#size [batch_size, 28, 28, 32] filter数量为32（经验值）
#layer2: 池化层  2 *  2 的池化核 

In [15]:
def cnn_model_func(features, labels, mode):
    
    #input_layer
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])
    
    #conv1
    conv1 = tf.layers.conv2d(
        inputs = input_layer,
        filters = 32,
        kernel_size = 5,
        padding = "same",
        activation = tf.nn.relu)
    
    #pool1
    pool1 = tf.layers.max_pooling2d(
        inputs = conv1, 
        pool_size = [2, 2], 
        strides = 2)
    
    #conv2
    conv2 = tf.layers.conv2d(
        inputs = pool1,
        filters = 64,
        kernel_size = 5,
        padding = "same",
        activation = tf.nn.relu)
    
    #pool2
    pool2 = tf.layers.max_pooling2d(
        inputs = conv2,
        pool_size = [2, 2],
        strides = 2)
    
    
    #Dense Layer
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    
    #dropout
    dropout = tf.layers.dropout(
    inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
    
    #Logits Layer
    logits = tf.layers.dense(inputs=dropout, units=10)
    
    predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
                loss=loss,
                global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


    

In [21]:
def main(unused_argv):
    # Load training and eval data
    mnist = input_data.read_data_sets("MNIST_data/", one_hot=False)
    train_data = mnist.train.images # Returns np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images # Returns np.array
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    
    # Create the Estimator
    mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_func, model_dir="/tmp/mnist_convnet_model")
    
    # Set up logging for predictions
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)
    
    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": train_data},
        y=train_labels,
        batch_size=100,
        num_epochs=None,
        shuffle=True)
    
    mnist_classifier.train(
        input_fn=train_input_fn,
        steps=20000,
        hooks=[logging_hook])

In [22]:
main(0)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000002A085F856D8>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:G

INFO:tensorflow:loss = 2.2810762, step = 0
INFO:tensorflow:probabilities = [[0.10716023 0.09901887 0.10711253 0.12879464 0.08940974 0.08496679
  0.09440199 0.10522549 0.09354793 0.09036174]
 [0.10892176 0.11121051 0.09201674 0.12211426 0.08660614 0.09806723
  0.08831606 0.09952291 0.09889385 0.09433053]
 [0.10334764 0.10591343 0.10877462 0.10351801 0.08784987 0.09454412
  0.09575313 0.09785912 0.09187287 0.11056715]
 [0.11300133 0.09333794 0.08675699 0.10884126 0.09410036 0.09931863
  0.10177545 0.09500691 0.11226816 0.09559298]
 [0.11826225 0.10083293 0.10007478 0.09696192 0.09065984 0.09309332
  0.08698322 0.1053133  0.1041676  0.10365085]
 [0.1141101  0.07891811 0.09609793 0.11292709 0.09824509 0.08753356
  0.10090578 0.10782557 0.1028042  0.10063249]
 [0.10188164 0.09711264 0.10418002 0.11169151 0.08430059 0.08759412
  0.09931622 0.10357711 0.11399641 0.09634973]
 [0.11601407 0.10735691 0.0887998  0.11503785 0.0830731  0.09077583
  0.10563204 0.09541044 0.09249946 0.10540048]
 [0.0

INFO:tensorflow:global_step/sec: 221.999
INFO:tensorflow:probabilities = [[0.12033213 0.09498136 0.10617958 0.11714378 0.08021443 0.08658656
  0.09442172 0.11545371 0.09645208 0.0882346 ]
 [0.12435216 0.09523185 0.09320154 0.12070448 0.08662691 0.09041321
  0.08439967 0.1025102  0.09388797 0.10867207]
 [0.09597589 0.10327434 0.0894584  0.12297558 0.08987018 0.07890113
  0.11574753 0.10510238 0.1000819  0.09861273]
 [0.10242083 0.09413154 0.0999309  0.12772615 0.09488241 0.09767624
  0.09331381 0.09369877 0.10488972 0.09132964]
 [0.11475108 0.08437023 0.10718033 0.12344186 0.08045296 0.0946382
  0.09340894 0.10443996 0.106465   0.09085152]
 [0.09914476 0.10234681 0.10708488 0.10047074 0.09488107 0.09682193
  0.09480571 0.10347898 0.1025974  0.09836771]
 [0.09963785 0.09373691 0.10863411 0.13028456 0.08270111 0.08881475
  0.09647689 0.1062765  0.09693774 0.09649957]
 [0.10119872 0.10216413 0.09931114 0.11223861 0.08644851 0.09862936
  0.08796804 0.10714144 0.11271847 0.09218155]
 [0.1082

INFO:tensorflow:loss = 2.2763436, step = 100 (0.450 sec)
INFO:tensorflow:probabilities = [[0.12021076 0.08773882 0.09396809 0.11967132 0.0809321  0.08579939
  0.10038593 0.10380243 0.11549445 0.09199673]
 [0.09946522 0.08251916 0.09527772 0.1019446  0.08923331 0.09529951
  0.10122753 0.11216137 0.11987792 0.10299359]
 [0.10725231 0.09331978 0.09484964 0.11775062 0.09334488 0.09028648
  0.10363808 0.09295545 0.10298736 0.10361537]
 [0.1081581  0.09619297 0.10169587 0.10545979 0.09487911 0.10214356
  0.1063785  0.104331   0.08493234 0.09582875]
 [0.1127269  0.10622974 0.09759793 0.10208202 0.09005515 0.0960655
  0.08975142 0.10281397 0.09790111 0.10477629]
 [0.10730478 0.10254393 0.10084187 0.09978447 0.08504985 0.09123695
  0.10097998 0.10659305 0.11195771 0.09370744]
 [0.11533279 0.08594039 0.10264358 0.11761237 0.08509983 0.07570138
  0.09668549 0.11111027 0.12383522 0.08603858]
 [0.11739475 0.0969726  0.10667606 0.10721521 0.07925563 0.0899298
  0.09402562 0.09417734 0.10616174 0.108

INFO:tensorflow:global_step/sec: 290.199
INFO:tensorflow:probabilities = [[0.12926316 0.10312678 0.10312366 0.10635918 0.07712607 0.09118638
  0.10150457 0.08785214 0.10345083 0.0970073 ]
 [0.10160644 0.08974596 0.10322626 0.13337982 0.08169291 0.0887451
  0.09669518 0.10561232 0.11061589 0.08868005]
 [0.10850681 0.09723091 0.09360663 0.1047304  0.0871368  0.09847633
  0.09941173 0.09865598 0.10721423 0.10503019]
 [0.09612163 0.10933157 0.09783566 0.11549265 0.09010386 0.09035764
  0.09572237 0.10272638 0.09386749 0.10844074]
 [0.11108322 0.10849194 0.10649648 0.10600986 0.09159604 0.09160793
  0.08342364 0.10836626 0.09990148 0.09302324]
 [0.11406174 0.0868257  0.09827622 0.11445518 0.08792095 0.10279706
  0.10561866 0.09204412 0.09379032 0.10421003]
 [0.11214977 0.09820122 0.09891447 0.1117086  0.09116714 0.10117421
  0.09020246 0.0990288  0.09311797 0.10433528]
 [0.12065502 0.09201312 0.094637   0.10176031 0.08334478 0.08638421
  0.0946601  0.11467882 0.10967197 0.10219473]
 [0.1451

...

INFO:tensorflow:global_step/sec: 286.176
INFO:tensorflow:probabilities = [[0.00033032 0.00124951 0.00684386 0.08674303 0.00028486 0.00743654
  0.00029993 0.00020972 0.89623517 0.00036704]
 [0.00007698 0.00000859 0.0127209  0.00684967 0.00000032 0.00016804
  0.00004775 0.00000014 0.9801062  0.00002153]
 [0.00020915 0.00078936 0.00003914 0.20882754 0.00687519 0.64572704
  0.00024771 0.00062856 0.13502839 0.00162785]
 [0.00000154 0.00000277 0.00027652 0.9985514  0.00000005 0.00116147
  0.00000001 0.00000026 0.00000545 0.00000062]
 [0.00073966 0.00094196 0.00023909 0.0003836  0.00000027 0.00000773
  0.00000639 0.00001509 0.99765706 0.00000919]
 [0.0000001  0.00000037 0.0005523  0.9993839  0.00000011 0.00001827
  0.00000002 0.00000049 0.00004222 0.00000226]
 [0.00001271 0.00002108 0.00310935 0.97115546 0.00000022 0.00040429
  0.00000004 0.00038105 0.00480689 0.02010895]
 [0.9839446  0.00000034 0.00003739 0.00000029 0.00250443 0.00018608
  0.01322829 0.00000194 0.00001379 0.00008275]
 [0.000

INFO:tensorflow:loss = 0.08386558, step = 19800 (0.346 sec)
INFO:tensorflow:probabilities = [[0.0000183  0.9961124  0.00008787 0.00039753 0.00142554 0.0000273
  0.00030156 0.00025232 0.00029876 0.00107831]
 [0.00290463 0.00006477 0.00517473 0.96576214 0.00003258 0.00306976
  0.00001697 0.00001735 0.01951501 0.00344205]
 [0.00000098 0.00000132 0.00011142 0.00050296 0.00003643 0.00001313
  0.00000187 0.00000122 0.9992218  0.00010887]
 [0.01185639 0.00025895 0.00072557 0.04262775 0.00000599 0.938371
  0.00004026 0.0019605  0.00187411 0.00227947]
 [0.06237989 0.00591717 0.01676595 0.2602725  0.0002186  0.62656534
  0.00253085 0.01238385 0.00040948 0.01255637]
 [0.99998105 0.00000011 0.00000334 0.00000252 0.         0.00000563
  0.00000447 0.00000026 0.00000227 0.00000032]
 [0.00000001 0.00000011 0.00026611 0.9997142  0.00000006 0.00000416
  0.00000001 0.00000003 0.00001528 0.00000011]
 [0.00228048 0.00036299 0.00332228 0.97416514 0.00000114 0.01814293
  0.00001737 0.00002871 0.0015571  0.0

INFO:tensorflow:global_step/sec: 290.173
INFO:tensorflow:probabilities = [[0.000001   0.00037246 0.9902152  0.00235545 0.00000614 0.00000123
  0.00000725 0.00662964 0.0004114  0.00000036]
 [0.9980233  0.00000003 0.00000845 0.00000001 0.         0.00166281
  0.00026472 0.         0.0000408  0.        ]
 [0.00001512 0.00000008 0.00003129 0.00000026 0.00003684 0.00005408
  0.99981624 0.00000001 0.00004577 0.00000034]
 [0.00000028 0.         0.00000149 0.         0.00000064 0.0000006
  0.9999937  0.         0.00000336 0.00000003]
 [0.00000059 0.00000084 0.99928564 0.00071162 0.00000004 0.00000016
  0.00000013 0.00000062 0.00000046 0.00000002]
 [0.00000006 0.00004185 0.00002714 0.00063588 0.9945081  0.00000576
  0.00000217 0.00040369 0.00052163 0.00385378]
 [0.00140014 0.00319428 0.00989713 0.9598975  0.00015144 0.00221009
  0.0004119  0.00048609 0.00749595 0.01485541]
 [0.00000214 0.00014646 0.99209964 0.00754935 0.00000075 0.00000267
  0.00000575 0.00016575 0.00002691 0.00000046]
 [0.0000

INFO:tensorflow:loss = 0.12751767, step = 19900 (0.344 sec)
INFO:tensorflow:probabilities = [[0.00000552 0.00000005 0.00000539 0.00000008 0.00006216 0.00000309
  0.99992    0.         0.00000368 0.00000003]
 [0.00052596 0.00033495 0.02538299 0.00135412 0.92856747 0.00092125
  0.00110708 0.00141274 0.01159548 0.02879791]
 [0.00001118 0.00013884 0.00008695 0.00147608 0.03626053 0.00055718
  0.00000802 0.0059333  0.00203877 0.9534892 ]
 [0.00225825 0.00489489 0.00360789 0.00140018 0.00419234 0.00071748
  0.0000904  0.8726015  0.00156462 0.10867246]
 [0.00000011 0.00000011 0.00000907 0.00000497 0.00000016 0.00000006
  0.         0.99979454 0.00000166 0.00018934]
 [0.8838898  0.0005066  0.01441932 0.00193843 0.00103681 0.00308073
  0.08535512 0.00774708 0.00010936 0.00191679]
 [0.0000798  0.00000083 0.00144378 0.00035299 0.01344529 0.00198239
  0.00007103 0.04714046 0.00221788 0.93326557]
 [0.00000936 0.01024842 0.9869326  0.0019289  0.0000019  0.00000729
  0.00000578 0.00000111 0.00086387 

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.10636061.
